In [1]:
%matplotlib inline
import numpy as np
import matplotlib.pyplot as plt
import matplotlib as mpl
import gdal
import osr
import os

In [2]:
def cut_and_paste(arr):
    halves = np.split(arr, 2, axis = -1)
    res = np.concatenate((halves[1], halves[0]), axis = -1)
    return res

def save_to_tiff(arr, filepath):
    arr_2 = cut_and_paste(arr)
    nbands, nrows, ncols = arr_2.shape
    xmin, ymin, xmax, ymax = [-180, -90, 180, 90]
    xres = (xmax - xmin) / float(ncols)
    yres = (ymax - ymin) / float(nrows)
    geotransform = (xmin, xres, 0, ymax, 0, -yres)
    raster = gdal.GetDriverByName('GTiff').Create(filepath, ncols, nrows, nbands, gdal.GDT_Float32)
    raster.SetGeoTransform(geotransform)
    srs = osr.SpatialReference()
    srs.ImportFromEPSG(4326)
    raster.SetProjection( srs.ExportToWkt() )
    for nband in range(nbands):
        outBand = raster.GetRasterBand(nband + 1)
        outBand.WriteArray(np.flipud(np.squeeze(arr_2[nband, :, :])))
    raster = None
    return True


In [3]:
from tempfile import NamedTemporaryFile
from google.cloud import storage
storage_client = storage.Client.from_service_account_json('credentials.json')
bucket = storage_client.get_bucket('nex-gddp')

# decadal measures
models = ["ACCESS1-0", "BNU-ESM", "CCSM4", "CESM1-BGC", "CNRM-CM5", "CSIRO-Mk3-6-0", "CanESM2", "GFDL-CM3", "GFDL-ESM2G", "GFDL-ESM2M", "IPSL-CM5A-LR", "IPSL-CM5A-MR", "MIROC-ESM-CHEM", "MIROC-ESM", "MIROC5", "MPI-ESM-LR", "MPI-ESM-MR", "MRI-CGCM3", "NorESM1-M", "bcc-csm1-1", "inmcm4"]
years = list(range(1975, 1985))

def output_array(context, scenario, models, years, varnames, prefix):
    ensemble_arr = []
    # Beginning with each model
    for model in models:
        print("Processing model " + model)
        model_arr = []
        # And for every year needed
        for year in years:
            # We download the file to a tempfile
            path = scenario + '/'  + scenario + '_' + str(year) + '_' + model + '_processed_' + context + '.npy'
            print(path)
            blob = bucket.get_blob( path )
            with NamedTemporaryFile() as temp:
                blob.download_to_file(temp)
                # And load it into an ndarray
                arr = np.load(temp.name)
                # That we store into a single list
                model_arr.append(arr)
        # After we are done with the downloads, we stack each
        # of the results in a single ndarray, along a new first axis
        model_stack = np.stack(model_arr)
        model_temp_avgs = []
        # For each indicator (ax 1), we'll calculate first the mean across the time axis,
        print("Stacking and averaging")
        for i in range(model_stack.shape[1]):
            indicator = model_stack[:, i, :, :]
            model_temp_avg = np.mean(indicator, axis = 0)
            model_temp_avgs.append(model_temp_avg)
        model_temp_avgs_stack = np.stack(model_temp_avgs)
        print(model_temp_avgs_stack.shape)
        ensemble_arr.append(model_temp_avgs_stack)
    ensemble_stack = np.stack(ensemble_arr)
    print(ensemble_stack.shape)
    # then the 25-75 percentiles across the models - out of the prior loop
    print("Calculating avg and percentile")
    result_avg = np.mean(ensemble_stack, axis = 0)
    result_p25 = np.percentile(ensemble_stack, axis=0, q=25)
    result_p75 = np.percentile(ensemble_stack, axis=0, q=75)
    result = np.stack((result_p25, result_avg, result_p75))
    # Finally, for each of the indicators (ax 1) we're going to store the avgs
    # and percentiles in a geotiff - and upload it to gcloud
    for index, varname in zip(list(range(result.shape[1])), varnames):
        #print(index, varname)
        indicator = result[:, index, :, :]
        with NamedTemporaryFile(suffix=".tiff") as temp_res:
            save_to_tiff(indicator, temp_res.name)
            print(varname)
            print(temp_res.name)
            output_filename = f'{prefix}_{scenario}_{years[0]}_{years[-1]}_{varname}.tiff'
            blob = bucket.blob('results/' + scenario + '/' + output_filename)
            blob.upload_from_filename(temp_res.name)
            print(blob)
    return result
                               

In [4]:
def process_decadal(context, year_from, scenario, varnames, models = models):
    result = output_array(
        context,
        scenario,
        models,
        list(range(year_from, year_from + 10)),
        varnames,
        "decadal_test"
    )    
    return result

In [5]:
def process_30_y(context, year_from, scenario, varnames, models = models):
    result = output_array(
        context,
        scenario,
        models,
        list(range(year_from, year_from + 30)),
        varnames,
        "30_y_test"
    )    
    return result

In [6]:
def mo_to_str(i):
    return ['jan', 'feb', 'march', 'april', 'may', 'june', 'july', 'aug', 'sept', 'oct', 'nov', 'dec'][i]

bucket = storage_client.get_bucket('nex-gddp')

def process_monthly_tasavg(year_from, scenario, models = models):
    # For each month, starting from year_from in the scenario
    str_months = range(12)
    print(str_months)
    for month in str_months:
    # (January, February)
        # For every model
        all_models_tasavg = []
        for model in models:
            print(f'Downloading files for {model}, {month}')
            # Download files: All ACCESS1-0 january files from year_from, to 
            # year_from + 3
            # Tasavg
            tasavg_monthly = []
            for year in range(year_from, year_from + 30):
                print(f"Downloading {year}")
                # Get file
                tasavg_url = f'/monthly/{scenario}/{scenario}_{str(year)}_{str(month).zfill(2)}_{mo_to_str(month)}_{model}_monthly_tasavg_processed.npy'
                print(tasavg_url)
                # Stack and average
                tasavg_blob = bucket.get_blob( tasavg_url )
                print(tasavg_blob)
                with NamedTemporaryFile(delete = False) as temp:
                    tasavg_blob.download_to_file(temp)
                    print(temp.name)
                    temp.close()
                    # And load it into an ndarray
                    arr = np.load(temp.name)
                    # That we store into a single list
                    tasavg_monthly.append(arr)
                    os.remove(temp.name)
            model_tasavg_avg = np.stack(tasavg_monthly)
            print("Per model shape:")
            print(model_tasavg_avg.shape)
            all_models_tasavg.append(np.mean(model_tasavg_avg, axis = 0))
        print("SHAPE")
        all_models_tasavg_stack = np.stack(all_models_tasavg)
        print(all_models_tasavg_stack.shape)
        
        tasavg_avg_across_models = np.mean(all_models_tasavg_stack, axis = 0)
        tasavg_q25_across_models = np.percentile(all_models_tasavg_stack, axis = 0, q = 25)
        tasavg_q75_across_models = np.percentile(all_models_tasavg_stack, axis = 0, q = 75)
        
        final_tasavg_stack = np.stack([
            tasavg_q25_across_models,
            tasavg_avg_across_models,
            tasavg_q75_across_models
        ])
        
        # np.save(f'{year_from}_{scenario}_monthly_tasavg.npy', final_tasavg_stack)
        save_to_tiff(final_tasavg_stack, f'{year_from}_{scenario}_{str(month).zfill(2)}_monthly_tasavg.tiff')
        # And stack calculate average, q25 and q75 across all models for every month

In [7]:
def process_monthly_tasmin(year_from, scenario, models = models):
    # For each month, starting from year_from in the scenario
    str_months = range(12)
    print(str_months)
    for month in str_months:
    # (January, February)
        # For every model
        all_models_tasmin = []
        for model in models:
            print(f'Downloading files for {model}, {month}')
            # Download files: All ACCESS1-0 january files from year_from, to 
            # year_from + 3
            # tasmin
            tasmin_monthly = []
            for year in range(year_from, year_from + 30):
                print(f"Downloading {year}")
                # Get file
                tasmin_url = f'/monthly/{scenario}/{scenario}_{str(year)}_{str(month).zfill(2)}_{mo_to_str(month)}_{model}_annual_tasmin_processed.npy'
                print(tasmin_url)
                # Stack and average
                tasmin_blob = bucket.get_blob( tasmin_url )
                print(tasmin_blob)
                with NamedTemporaryFile(delete = False) as temp:
                    tasmin_blob.download_to_file(temp)
                    print(temp.name)
                    temp.close()
                    # And load it into an ndarray
                    arr = np.load(temp.name)
                    os.remove(temp.name)
                    # That we store into a single list
                    tasmin_monthly.append(arr)
            model_tasmin_avg = np.stack(tasmin_monthly)
            print("Per model shape:")
            print(model_tasmin_avg.shape)
            all_models_tasmin.append(np.mean(model_tasmin_avg, axis = 0))
        print("SHAPE")
        all_models_tasmin_stack = np.stack(all_models_tasmin)
        print(all_models_tasmin_stack.shape)
        
        tasmin_avg_across_models = np.mean(all_models_tasmin_stack, axis = 0)
        tasmin_q25_across_models = np.percentile(all_models_tasmin_stack, axis = 0, q = 25)
        tasmin_q75_across_models = np.percentile(all_models_tasmin_stack, axis = 0, q = 75)
        
        final_tasmin_stack = np.stack([
            tasmin_q25_across_models,
            tasmin_avg_across_models,
            tasmin_q75_across_models
        ])
        
        # np.save(f'{year_from}_{scenario}_monthly_tasmin.npy', final_tasmin_stack)
        save_to_tiff(final_tasmin_stack, f'{year_from}_{scenario}_{str(month).zfill(2)}_monthly_tasmin.tiff')
        # And stack calculate average, q25 and q75 across all models for every month

In [8]:
def process_monthly_tasmax(year_from, scenario, models = models):
    # For each month, starting from year_from in the scenario
    str_months = range(12)
    print(str_months)
    for month in str_months:
    # (January, February)
        # For every model
        all_models_tasmax = []
        for model in models:
            print(f'Downloading files for {model}, {month}')
            # Download files: All ACCESS1-0 january files from year_from, to 
            # year_from + 3
            # tasmax
            tasmax_monthly = []
            for year in range(year_from, year_from + 30):
                print(f"Downloading {year}")
                # Get file
                tasmax_url = f'/monthly/{scenario}/{scenario}_{str(year)}_{str(month).zfill(2)}_{mo_to_str(month)}_{model}_annual_tasmax_processed.npy'
                print(tasmax_url)
                # Stack and average
                tasmax_blob = bucket.get_blob( tasmax_url )
                print(tasmax_blob)
                with NamedTemporaryFile(delete = False) as temp:
                    tasmax_blob.download_to_file(temp)
                    print(temp.name)
                    temp.close()
                    # And load it into an ndarray
                    arr = np.load(temp.name)
                    # That we store into a single list
                    tasmax_monthly.append(arr)
            model_tasmax_avg = np.stack(tasmax_monthly)
            print("Per model shape:")
            print(model_tasmax_avg.shape)
            all_models_tasmax.append(np.mean(model_tasmax_avg, axis = 0))
        print("SHAPE")
        all_models_tasmax_stack = np.stack(all_models_tasmax)
        print(all_models_tasmax_stack.shape)
        
        tasmax_avg_across_models = np.mean(all_models_tasmax_stack, axis = 0)
        tasmax_q25_across_models = np.percentile(all_models_tasmax_stack, axis = 0, q = 25)
        tasmax_q75_across_models = np.percentile(all_models_tasmax_stack, axis = 0, q = 75)
        
        final_tasmax_stack = np.stack([
            tasmax_q25_across_models,
            tasmax_avg_across_models,
            tasmax_q75_across_models
        ])
        
        # np.save(f'{year_from}_{scenario}_monthly_tasmax.npy', final_tasmax_stack)
        save_to_tiff(final_tasmax_stack, f'{year_from}_{scenario}_{str(month).zfill(2)}_monthly_tasmax.tiff')
        # And stack calculate average, q25 and q75 across all models for every month

In [9]:
def process_monthly_pr(year_from, scenario, models = models):
    # For each month, starting from year_from in the scenario
    str_months = range(12)
    print(str_months)
    for month in str_months:
    # (January, February)
        # For every model
        all_models_pr = []
        for model in models:
            print(f'Downloading files for {model}, {month}')
            # Download files: All ACCESS1-0 january files from year_from, to 
            # year_from + 3
            # pr
            pr_monthly = []
            for year in range(year_from, year_from + 30):
                print(f"Downloading {year}")
                # Get file
                pr_url = f'/monthly/{scenario}/{scenario}_{str(year)}_{str(month).zfill(2)}_{mo_to_str(month)}_{model}_annual_pr_processed.npy'
                print(pr_url)
                # Stack and average
                pr_blob = bucket.get_blob( pr_url )
                print(pr_blob)
                with NamedTemporaryFile(delete = False) as temp:
                    pr_blob.download_to_file(temp)
                    print(temp.name)
                    temp.close()
                    # And load it into an ndarray
                    arr = np.load(temp.name)
                    # That we store into a single list
                    pr_monthly.append(arr)
            model_pr_avg = np.stack(pr_monthly)
            print("Per model shape:")
            print(model_pr_avg.shape)
            all_models_pr.append(np.mean(model_pr_avg, axis = 0))
        print("SHAPE")
        all_models_pr_stack = np.stack(all_models_pr)
        print(all_models_pr_stack.shape)
        
        pr_avg_across_models = np.mean(all_models_pr_stack, axis = 0)
        pr_q25_across_models = np.percentile(all_models_pr_stack, axis = 0, q = 25)
        pr_q75_across_models = np.percentile(all_models_pr_stack, axis = 0, q = 75)
        
        final_pr_stack = np.stack([
            pr_q25_across_models,
            pr_avg_across_models,
            pr_q75_across_models
        ])
        
        # np.save(f'{year_from}_{scenario}_monthly_pr.npy', final_pr_stack)
        save_to_tiff(final_pr_stack, f'{year_from}_{scenario}_{str(month).zfill(2)}_monthly_pr.tiff')
        # And stack calculate average, q25 and q75 across all models for every month

In [10]:
#process_monthly_pr(1971, 'historical')
#process_monthly_tasavg(1971, 'historical')
process_monthly_tasmax(1971, 'historical')
process_monthly_tasmin(1971, 'historical')

process_monthly_pr(2021, 'rcp45')
process_monthly_tasavg(2021, 'rcp45')
process_monthly_tasmax(2021, 'rcp45')
process_monthly_tasmin(2021, 'rcp45')

process_monthly_pr(2051, 'rcp45')
process_monthly_tasavg(2051, 'rcp45')
process_monthly_tasmax(2051, 'rcp45')
process_monthly_tasmin(2051, 'rcp45')

process_monthly_pr(2021, 'rcp85')
process_monthly_tasavg(2021, 'rcp85')
process_monthly_tasmax(2021, 'rcp85')
process_monthly_tasmin(2021, 'rcp85')

process_monthly_pr(2051, 'rcp85')
process_monthly_tasavg(2051, 'rcp85')
process_monthly_tasmax(2051, 'rcp85')
process_monthly_tasmin(2051, 'rcp85')


range(0, 12)
/monthly/historical/historical_1971_00_jan_ACCESS1-0_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1971_00_jan_ACCESS1-0_annual_tasmax_processed.npy>
/tmp/tmpk1bc2bf_
/monthly/historical/historical_1972_00_jan_ACCESS1-0_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1972_00_jan_ACCESS1-0_annual_tasmax_processed.npy>
/tmp/tmpfjkdnviy
/monthly/historical/historical_1973_00_jan_ACCESS1-0_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1973_00_jan_ACCESS1-0_annual_tasmax_processed.npy>
/tmp/tmp8e0l3gs1
/monthly/historical/historical_1974_00_jan_ACCESS1-0_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1974_00_jan_ACCESS1-0_annual_tasmax_processed.npy>
/tmp/tmpvh2dp5xl
/monthly/historical/historical_1975_00_jan_ACCESS1-0_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1975_00_jan_ACCESS1-0_annual_tasmax_processed.npy>
/tmp/tmpzju_50e6
/m

/tmp/tmpdmb6dl08
/monthly/historical/historical_1979_00_jan_BNU-ESM_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1979_00_jan_BNU-ESM_annual_tasmax_processed.npy>
/tmp/tmpo0jj7k2r
/monthly/historical/historical_1980_00_jan_BNU-ESM_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1980_00_jan_BNU-ESM_annual_tasmax_processed.npy>
/tmp/tmpwbt5ixo9
/monthly/historical/historical_1981_00_jan_BNU-ESM_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1981_00_jan_BNU-ESM_annual_tasmax_processed.npy>
/tmp/tmpm5qfzpgv
/monthly/historical/historical_1982_00_jan_BNU-ESM_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1982_00_jan_BNU-ESM_annual_tasmax_processed.npy>
/tmp/tmp801tti2s
/monthly/historical/historical_1983_00_jan_BNU-ESM_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1983_00_jan_BNU-ESM_annual_tasmax_processed.npy>
/tmp/tmp7tnq23p4
/monthly/historica

/tmp/tmpzeyqrrj0
/monthly/historical/historical_1989_00_jan_CCSM4_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1989_00_jan_CCSM4_annual_tasmax_processed.npy>
/tmp/tmpx3j5wojw
/monthly/historical/historical_1990_00_jan_CCSM4_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1990_00_jan_CCSM4_annual_tasmax_processed.npy>
/tmp/tmpgsgr6f4w
/monthly/historical/historical_1991_00_jan_CCSM4_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1991_00_jan_CCSM4_annual_tasmax_processed.npy>
/tmp/tmpfzmh99qo
/monthly/historical/historical_1992_00_jan_CCSM4_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1992_00_jan_CCSM4_annual_tasmax_processed.npy>
/tmp/tmp12busfoo
/monthly/historical/historical_1993_00_jan_CCSM4_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1993_00_jan_CCSM4_annual_tasmax_processed.npy>
/tmp/tmpcj_bbj50
/monthly/historical/historical_1994_00

/tmp/tmpp13fz4c4
/monthly/historical/historical_1998_00_jan_CESM1-BGC_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1998_00_jan_CESM1-BGC_annual_tasmax_processed.npy>
/tmp/tmpji3yvhev
/monthly/historical/historical_1999_00_jan_CESM1-BGC_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1999_00_jan_CESM1-BGC_annual_tasmax_processed.npy>
/tmp/tmpqka21c5y
/monthly/historical/historical_2000_00_jan_CESM1-BGC_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_2000_00_jan_CESM1-BGC_annual_tasmax_processed.npy>
/tmp/tmpszmz09n4
Per model shape:
(30, 720, 1440)
/monthly/historical/historical_1971_00_jan_CNRM-CM5_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1971_00_jan_CNRM-CM5_annual_tasmax_processed.npy>
/tmp/tmpwlt8zj4x
/monthly/historical/historical_1972_00_jan_CNRM-CM5_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1972_00_jan_CNRM-CM5_annual_tasmax_p

/tmp/tmp7cn3e6u7
/monthly/historical/historical_1976_00_jan_CSIRO-Mk3-6-0_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1976_00_jan_CSIRO-Mk3-6-0_annual_tasmax_processed.npy>
/tmp/tmp1j1v8xu1
/monthly/historical/historical_1977_00_jan_CSIRO-Mk3-6-0_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1977_00_jan_CSIRO-Mk3-6-0_annual_tasmax_processed.npy>
/tmp/tmpjqhiqfmr
/monthly/historical/historical_1978_00_jan_CSIRO-Mk3-6-0_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1978_00_jan_CSIRO-Mk3-6-0_annual_tasmax_processed.npy>
/tmp/tmpdsp8un8u
/monthly/historical/historical_1979_00_jan_CSIRO-Mk3-6-0_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1979_00_jan_CSIRO-Mk3-6-0_annual_tasmax_processed.npy>
/tmp/tmp1brjw5sh
/monthly/historical/historical_1980_00_jan_CSIRO-Mk3-6-0_annual_tasmax_processed.npy
<Blob: nex-gddp, /monthly/historical/historical_1980_00_jan_CSIRO-Mk3-6-0_annu

...

/tmp/tmpeeb8n4gf
/monthly/rcp45/rcp45_2038_11_dec_MIROC5_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2038_11_dec_MIROC5_annual_pr_processed.npy>
/tmp/tmpxcgpuy3i
/monthly/rcp45/rcp45_2039_11_dec_MIROC5_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2039_11_dec_MIROC5_annual_pr_processed.npy>
/tmp/tmpzyb8uzb4
/monthly/rcp45/rcp45_2040_11_dec_MIROC5_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2040_11_dec_MIROC5_annual_pr_processed.npy>
/tmp/tmpqjqajcw0
/monthly/rcp45/rcp45_2041_11_dec_MIROC5_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2041_11_dec_MIROC5_annual_pr_processed.npy>
/tmp/tmpaj2614cs
/monthly/rcp45/rcp45_2042_11_dec_MIROC5_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2042_11_dec_MIROC5_annual_pr_processed.npy>
/tmp/tmps97kgl8j
/monthly/rcp45/rcp45_2043_11_dec_MIROC5_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2043_11_dec_MIROC5_annual_pr_processed.npy>
/tmp/tmpskpffmr3
/mont

/tmp/tmp_6tzqiex
/monthly/rcp45/rcp45_2022_11_dec_MPI-ESM-MR_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2022_11_dec_MPI-ESM-MR_annual_pr_processed.npy>
/tmp/tmp1z_ouqgl
/monthly/rcp45/rcp45_2023_11_dec_MPI-ESM-MR_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2023_11_dec_MPI-ESM-MR_annual_pr_processed.npy>
/tmp/tmp3dwe2wpr
/monthly/rcp45/rcp45_2024_11_dec_MPI-ESM-MR_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2024_11_dec_MPI-ESM-MR_annual_pr_processed.npy>
/tmp/tmpegavhxj4
/monthly/rcp45/rcp45_2025_11_dec_MPI-ESM-MR_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2025_11_dec_MPI-ESM-MR_annual_pr_processed.npy>
/tmp/tmp3ynxuz5r
/monthly/rcp45/rcp45_2026_11_dec_MPI-ESM-MR_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2026_11_dec_MPI-ESM-MR_annual_pr_processed.npy>
/tmp/tmpls0fjcky
/monthly/rcp45/rcp45_2027_11_dec_MPI-ESM-MR_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2027_11_dec_MPI-ESM-MR

/tmp/tmp2p91edxm
/monthly/rcp45/rcp45_2036_11_dec_MRI-CGCM3_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2036_11_dec_MRI-CGCM3_annual_pr_processed.npy>
/tmp/tmprytyti40
/monthly/rcp45/rcp45_2037_11_dec_MRI-CGCM3_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2037_11_dec_MRI-CGCM3_annual_pr_processed.npy>
/tmp/tmpwqkeubrw
/monthly/rcp45/rcp45_2038_11_dec_MRI-CGCM3_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2038_11_dec_MRI-CGCM3_annual_pr_processed.npy>
/tmp/tmpwf6gxiun
/monthly/rcp45/rcp45_2039_11_dec_MRI-CGCM3_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2039_11_dec_MRI-CGCM3_annual_pr_processed.npy>
/tmp/tmp0v3dspfj
/monthly/rcp45/rcp45_2040_11_dec_MRI-CGCM3_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2040_11_dec_MRI-CGCM3_annual_pr_processed.npy>
/tmp/tmp1xz4ii0c
/monthly/rcp45/rcp45_2041_11_dec_MRI-CGCM3_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2041_11_dec_MRI-CGCM3_annual_pr_p

/tmp/tmps7sbenr7
/monthly/rcp45/rcp45_2050_11_dec_NorESM1-M_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2050_11_dec_NorESM1-M_annual_pr_processed.npy>
/tmp/tmpb7iuppta
Per model shape:
(30, 720, 1440)
/monthly/rcp45/rcp45_2021_11_dec_bcc-csm1-1_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2021_11_dec_bcc-csm1-1_annual_pr_processed.npy>
/tmp/tmprbcwb21h
/monthly/rcp45/rcp45_2022_11_dec_bcc-csm1-1_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2022_11_dec_bcc-csm1-1_annual_pr_processed.npy>
/tmp/tmp_9ehhg_3
/monthly/rcp45/rcp45_2023_11_dec_bcc-csm1-1_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2023_11_dec_bcc-csm1-1_annual_pr_processed.npy>
/tmp/tmpixn276oq
/monthly/rcp45/rcp45_2024_11_dec_bcc-csm1-1_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp45/rcp45_2024_11_dec_bcc-csm1-1_annual_pr_processed.npy>
/tmp/tmp3imbm69r
/monthly/rcp45/rcp45_2025_11_dec_bcc-csm1-1_annual_pr_processed.npy
<Blob: nex-gddp, /monthly/rcp

OSError: [Errno 28] No space left on device